In [3]:
import os
os.chdir('D:/Ritika Agarwal/Hackathons/Analytics Vidhya/Innoplexus Online Hiring Hackathon Sentiment Analysis/')

In [4]:
%load_ext autoreload
%autoreload 2
%matplotlib inline

In [5]:
from fastai.imports import *

In [6]:
import pandas as pd
import numpy as np
import text_norm as tn
import model_evaluation_utils as meu
import nltk
import textblob
np.set_printoptions(precision=2, linewidth=80)

In [7]:
PATH = "D:/Ritika Agarwal/Hackathons/Analytics Vidhya/Innoplexus Online Hiring Hackathon Sentiment Analysis/"

In [114]:
def get_combined():
    df_train = pd.read_csv(f'{PATH}train_F3WbcTw.csv', low_memory=False)
    df_test=pd.read_csv(f'{PATH}test_tOlRoBf.csv', low_memory=False)
    df_test['sentiment'] = np.nan
    combined= df_train.append(df_test)
    combined.reset_index(inplace=True)
    combined.drop(['index','unique_hash'],inplace=True,axis=1)
    return combined

In [115]:
combined_df= get_combined()

In [116]:
combined_df.shape

(8203, 3)

In [118]:
combined_df.tail()

text        drug  sentiment
8198  Reply posted for Hippopostrous. We are sorry t...    remicade        NaN
8199  Aw Lorraine That's crap. What a shame you've h...     gilenya        NaN
8200  jskozio14\n That sounds like nonsense to me.  ...      opdivo        NaN
8201  It sounds like you're doing very well FG! I wo...     stelara        NaN
8202  Hi @rambles too! It’s such a hard decision, is...  cladribine        NaN

In [119]:
print(combined_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8203 entries, 0 to 8202
Data columns (total 3 columns):
text         8203 non-null object
drug         8203 non-null object
sentiment    5279 non-null float64
dtypes: float64(1), object(2)
memory usage: 192.3+ KB
None


In [120]:
combined_df_copy=combined_df

In [121]:
combined_df['drug'].value_counts()

ocrevus                         978
gilenya                         977
ocrelizumab                     602
entyvio                         486
humira                          458
remicade                        403
opdivo                          354
tarceva                         344
fingolimod                      343
keytruda                        314
cladribine                      300
tagrisso                        286
stelara                         267
alimta                          229
lucentis                        114
eylea                            98
cimzia                           86
avastin                          83
nivolumab                        73
crizotinib                       66
simponi                          66
vitrectomy                       64
alectinib                        62
erlotinib                        61
tecentriq                        51
pembrolizumab                    50
xalkori                          48
osimertinib                 

In [122]:
import nltk
stopword_list = nltk.corpus.stopwords.words('english')
# just to keep negation if any in bi-grams
stopword_list.remove('no')
stopword_list.remove('not')

# normalize our corpus
norm_corpus = tn.normalize_corpus(corpus=combined_df['text'], html_stripping=True, contraction_expansion=True, 
                                  accented_char_removal=True, text_lower_case=True, text_lemmatization=True, 
                                  text_stemming=False, special_char_removal=True, remove_digits=True,
                                  stopword_removal=True, stopwords=stopword_list)
combined_df['Clean Text'] = norm_corpus

In [8]:
df= pd.read_csv('train_F3WbcTw.csv')

In [9]:
df.shape

(5279, 4)

In [31]:
#reviews = np.array(df['text'])
#sentiments = np.array(df['sentiment'])

In [80]:
#df.head()

unique_hash  \
0  2e180be4c9214c1f5ab51fd8cc32bc80c9f612e0   
1  9eba8f80e7e20f3a2f48685530748fbfa95943e4   
2  fe809672251f6bd0d986e00380f48d047c7e7b76   
3  bd22104dfa9ec80db4099523e03fae7a52735eb6   
4  b227688381f9b25e5b65109dd00f7f895e838249   

                                                text        drug  sentiment  
0  Autoimmune diseases tend to come in clusters. ...     gilenya          2  
1  I can completely understand why you’d want to ...     gilenya          2  
2  Interesting that it only targets S1P-1/5 recep...  fingolimod          2  
3  Very interesting, grand merci. Now I wonder wh...     ocrevus          2  
4  Hi everybody, My latest MRI results for Brain ...     gilenya          1

In [10]:
total_nulls = df[df.text.str.strip() == ''].shape[0]
print("Empty documents:", total_nulls)

Empty documents: 0


In [11]:
import nltk
stopword_list = nltk.corpus.stopwords.words('english')
# just to keep negation if any in bi-grams
stopword_list.remove('no')
stopword_list.remove('not')

# normalize our corpus
norm_corpus = tn.normalize_corpus(corpus=df['text'], html_stripping=True, contraction_expansion=True, 
                                  accented_char_removal=True, text_lower_case=True, text_lemmatization=True, 
                                  text_stemming=False, special_char_removal=True, remove_digits=True,
                                  stopword_removal=True, stopwords=stopword_list)
df['Clean Text'] = norm_corpus

In [12]:
df.head()

unique_hash  \
0  2e180be4c9214c1f5ab51fd8cc32bc80c9f612e0   
1  9eba8f80e7e20f3a2f48685530748fbfa95943e4   
2  fe809672251f6bd0d986e00380f48d047c7e7b76   
3  bd22104dfa9ec80db4099523e03fae7a52735eb6   
4  b227688381f9b25e5b65109dd00f7f895e838249   

                                                text        drug  sentiment  \
0  Autoimmune diseases tend to come in clusters. ...     gilenya          2   
1  I can completely understand why you’d want to ...     gilenya          2   
2  Interesting that it only targets S1P-1/5 recep...  fingolimod          2   
3  Very interesting, grand merci. Now I wonder wh...     ocrevus          2   
4  Hi everybody, My latest MRI results for Brain ...     gilenya          1   

                                          Clean Text  
0  autoimmune disease tend come cluster gilenya f...  
1  completely understand would want try result re...  
2  interesting target sp receptor rather like fin...  
3  interesting grand merci wonder lemtrada ocrevu...  
4  hi everybody late mri result brain cervical co...

In [13]:
# test dataset
test_df= pd.read_csv('test_tOlRoBf.csv')
test_df.shape
test_df.head()

unique_hash  \
0  9e9a8166b84114aca147bf409f6f956635034c08   
1  e747e6822c867571afe7b907b51f0f2ca67b0e1a   
2  50b6d851bcff4f35afe354937949e9948975adf7   
3  7f82ec2176ae6ab0b5d20b5ffc767ac829f384ae   
4  8b37d169dee5bdae27060949242fb54feb6a7f7f   

                                                text        drug  
0  256 (previously stable on natalizumab), with 5...  fingolimod  
1  On fingolimod and have been since December 201...  fingolimod  
2  Apparently it's shingles! :-/ I do have a few ...      humira  
3  If the Docetaxel doing once a week x3 weeks th...    tagrisso  
4  CC, Stelara worked in a matter of days for me....     stelara

In [14]:
# normalize the test dataset
norm_corpus_test = tn.normalize_corpus(corpus=test_df['text'], html_stripping=True, contraction_expansion=True, 
                                  accented_char_removal=True, text_lower_case=True, text_lemmatization=True, 
                                  text_stemming=False, special_char_removal=True, remove_digits=True,
                                  stopword_removal=True, stopwords=stopword_list)
test_df['Clean Text'] = norm_corpus_test

In [15]:
test_df.head(10)

unique_hash  \
0  9e9a8166b84114aca147bf409f6f956635034c08   
1  e747e6822c867571afe7b907b51f0f2ca67b0e1a   
2  50b6d851bcff4f35afe354937949e9948975adf7   
3  7f82ec2176ae6ab0b5d20b5ffc767ac829f384ae   
4  8b37d169dee5bdae27060949242fb54feb6a7f7f   
5  b1950d27d94ceff4e9bf8c7d1fd4b11b35ede4d7   
6  abafc5b6c5aac6f777cf265e5c7dd80fb793e6bc   
7  e5550693e72a8335d723ca5fc64da91e1256fb0b   
8  ee8c500f6402331ff12b0b29d943b6d1699a0b8d   
9  d261600ba4fc022fac12748845deed56822ff195   

                                                text        drug  \
0  256 (previously stable on natalizumab), with 5...  fingolimod   
1  On fingolimod and have been since December 201...  fingolimod   
2  Apparently it's shingles! :-/ I do have a few ...      humira   
3  If the Docetaxel doing once a week x3 weeks th...    tagrisso   
4  CC, Stelara worked in a matter of days for me....     stelara   
5  Janssen Biotech, Inc. has just received FDA ap...     stelara   
6  I just had the, ” I thought things would be be...     ocrevus   
7  Dec.26 2018 (Basha Fowler) I was diagnosed in ...    tagrisso   
8  Hi, I started Gilenya about 7 weeks ago and ha...     gilenya   
9  My uncle is still going through treatment. 2 k...    keytruda   

                                          Clean Text  
0  previously stable natalizumab switching fingol...  
1  fingolimod since december way describe well li...  
2  apparently shingle red spot left breast appear...  
3  docetaxel week x week week claim less harsh ef...  
4  cc stelara work matter day gi willing jump hoo...  
5  janssen biotech inc receive fda approval new b...  
6  think thing would well one year ms talk husban...  
7  dec basha fowler diagnose rd week december egf...  
8  hi start gilenya week ago woeful anxiety time ...  
9  uncle still go treatment kind chemo keytruda r...

In [16]:
from sklearn.model_selection import train_test_split

train_corpus, test_corpus, train_label_nums, test_label_nums = train_test_split(np.array(df['Clean Text']), np.array(df['sentiment']),
                                                       test_size=0.33, random_state=42)

train_corpus.shape, test_corpus.shape

((3536,), (1743,))

In [17]:
train_label_nums

array([2, 1, 2, ..., 0, 2, 2], dtype=int64)

In [18]:
test_label_nums 

array([1, 2, 2, ..., 2, 2, 0], dtype=int64)

In [19]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import cross_val_score

# build BOW features on train articles
cv = CountVectorizer(binary=False, min_df=0.0, max_df=1.0)
cv_train_features = cv.fit_transform(train_corpus)

In [20]:
# transform test articles into features
cv_test_features = cv.transform(test_corpus)

In [21]:
print('BOW model:> Train features shape:', cv_train_features.shape, ' Test features shape:', cv_test_features.shape)

BOW model:> Train features shape: (3536, 27878)  Test features shape: (1743, 27878)


In [22]:
from sklearn.naive_bayes import MultinomialNB

mnb = MultinomialNB(alpha=1)
mnb.fit(cv_train_features, train_label_nums)
mnb_bow_cv_scores = cross_val_score(mnb, cv_train_features, train_label_nums, cv=5)
mnb_bow_cv_mean_score = np.mean(mnb_bow_cv_scores)
print('CV Accuracy (5-fold):', mnb_bow_cv_scores)
print('Mean CV Accuracy:', mnb_bow_cv_mean_score)
mnb_bow_test_score = mnb.score(cv_test_features, test_label_nums)
print('Test Accuracy:', mnb_bow_test_score)

CV Accuracy (5-fold): [0.61 0.58 0.57 0.59 0.61]
Mean CV Accuracy: 0.5921917379207444
Test Accuracy: 0.6190476190476191


In [23]:

from sklearn.linear_model import LogisticRegression

lr = LogisticRegression(penalty='l2', max_iter=100, C=1, random_state=42)
lr.fit(cv_train_features, train_label_nums)
lr_bow_cv_scores = cross_val_score(lr, cv_train_features, train_label_nums, cv=5)
lr_bow_cv_mean_score = np.mean(lr_bow_cv_scores)
print('CV Accuracy (5-fold):', lr_bow_cv_scores)
print('Mean CV Accuracy:', lr_bow_cv_mean_score)
lr_bow_test_score = lr.score(cv_test_features, test_label_nums)
print('Test Accuracy:', lr_bow_test_score)

C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\svm\base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_cla

CV Accuracy (5-fold): [0.68 0.68 0.68 0.68 0.69]
Mean CV Accuracy: 0.6798668231753573
Test Accuracy: 0.6901893287435457


In [24]:
from sklearn.svm import LinearSVC

svm = LinearSVC(penalty='l2', C=1, random_state=42)
svm.fit(cv_train_features, train_label_nums)
svm_bow_cv_scores = cross_val_score(svm, cv_train_features, train_label_nums, cv=5)
svm_bow_cv_mean_score = np.mean(svm_bow_cv_scores)
print('CV Accuracy (5-fold):', svm_bow_cv_scores)
print('Mean CV Accuracy:', svm_bow_cv_mean_score)
svm_bow_test_score = svm.score(cv_test_features, test_label_nums)
print('Test Accuracy:', svm_bow_test_score)

C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\svm\base.py:929: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


CV Accuracy (5-fold): [0.64 0.65 0.59 0.62 0.64]
Mean CV Accuracy: 0.6283859578601254
Test Accuracy: 0.6477337923121056


In [25]:
from sklearn.feature_extraction.text import TfidfVectorizer

# build BOW features on train articles
tv = TfidfVectorizer(use_idf=True, min_df=0.0, max_df=1.0)
tv_train_features = tv.fit_transform(train_corpus)

In [26]:

# transform test articles into features
tv_test_features = tv.transform(test_corpus)

In [27]:
print('TFIDF model:> Train features shape:', tv_train_features.shape, ' Test features shape:', tv_test_features.shape)

TFIDF model:> Train features shape: (3536, 27878)  Test features shape: (1743, 27878)


In [28]:

mnb = MultinomialNB(alpha=1)
mnb.fit(tv_train_features, train_label_nums)
mnb_tfidf_cv_scores = cross_val_score(mnb, tv_train_features, train_label_nums, cv=5)
mnb_tfidf_cv_mean_score = np.mean(mnb_tfidf_cv_scores)
print('CV Accuracy (5-fold):', mnb_tfidf_cv_scores)
print('Mean CV Accuracy:', mnb_tfidf_cv_mean_score)
mnb_tfidf_test_score = mnb.score(tv_test_features, test_label_nums)
print('Test Accuracy:', mnb_tfidf_test_score)

CV Accuracy (5-fold): [0.72 0.72 0.73 0.72 0.73]
Mean CV Accuracy: 0.7245480406290608
Test Accuracy: 0.7240390131956397


In [29]:
lr = LogisticRegression(penalty='l2', max_iter=100, C=1, random_state=42)
lr.fit(tv_train_features, train_label_nums)
lr_tfidf_cv_scores = cross_val_score(lr, tv_train_features, train_label_nums, cv=5)
lr_tfidf_cv_mean_score = np.mean(lr_tfidf_cv_scores)
print('CV Accuracy (5-fold):', lr_tfidf_cv_scores)
print('Mean CV Accuracy:', lr_tfidf_cv_mean_score)
lr_tfidf_test_score = lr.score(tv_test_features, test_label_nums)
print('Test Accuracy:', lr_tfidf_test_score)

C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


CV Accuracy (5-fold): [0.72 0.73 0.73 0.72 0.73]
Mean CV Accuracy: 0.7256795812323549
Test Accuracy: 0.7292025243832473


In [30]:
svm = LinearSVC(penalty='l2', C=1, random_state=42)
svm.fit(tv_train_features, train_label_nums)
svm_tfidf_cv_scores = cross_val_score(svm, tv_train_features, train_label_nums, cv=5)
svm_tfidf_cv_mean_score = np.mean(svm_tfidf_cv_scores)
print('CV Accuracy (5-fold):', svm_tfidf_cv_scores)
print('Mean CV Accuracy:', svm_tfidf_cv_mean_score)
svm_tfidf_test_score = svm.score(tv_test_features, test_label_nums)
print('Test Accuracy:', svm_tfidf_test_score)

CV Accuracy (5-fold): [0.72 0.72 0.72 0.69 0.72]
Mean CV Accuracy: 0.7137911671640539
Test Accuracy: 0.7177280550774526


In [31]:
pd.DataFrame([['Naive Bayes', mnb_bow_cv_mean_score, mnb_bow_test_score, 
               mnb_tfidf_cv_mean_score, mnb_tfidf_test_score],
              ['Logistic Regression', lr_bow_cv_mean_score, lr_bow_test_score, 
               lr_tfidf_cv_mean_score, lr_tfidf_test_score],
              ['Linear SVM', svm_bow_cv_mean_score, svm_bow_test_score, 
               svm_tfidf_cv_mean_score, svm_tfidf_test_score],
              ],
             columns=['Model', 'CV Score (TF)', 'Test Score (TF)', 'CV Score (TF-IDF)', 'Test Score (TF-IDF)'],
             ).T

0                    1           2
Model                Naive Bayes  Logistic Regression  Linear SVM
CV Score (TF)           0.592192             0.679867    0.628386
Test Score (TF)         0.619048             0.690189    0.647734
CV Score (TF-IDF)       0.724548              0.72568    0.713791
Test Score (TF-IDF)     0.724039             0.729203    0.717728

In [2]:
from sklearn.pipeline import Pipeline

In [32]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.naive_bayes import MultinomialNB
from sklearn.feature_extraction.text import TfidfVectorizer

mnb_pipeline = Pipeline([('tfidf', TfidfVectorizer()),('mnb', MultinomialNB())])

param_grid = {'tfidf__ngram_range': [(1, 1), (1, 2)], 'mnb__alpha': [1e-5, 1e-4, 1e-2, 1e-1, 1]}

gs_mnb = GridSearchCV(mnb_pipeline, param_grid, cv=5, verbose=2)
gs_mnb = gs_mnb.fit(train_corpus, train_label_nums)

Fitting 5 folds for each of 10 candidates, totalling 50 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 1) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 1), total=   0.6s


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.5s remaining:    0.0s


[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 1) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 1), total=   0.6s
[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 1) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 1), total=   0.6s
[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 1) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 1), total=   0.7s
[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 1) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 1), total=   0.7s
[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 2) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 2), total=   2.4s
[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 2) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 2), total=   2.4s
[CV] mnb__alpha=1e-05, tfidf__ngram_range=(1, 2) .....................
[CV] ...... mnb__alpha=1e-05, tfidf__ngram_range=(1, 2), total=   2.5s
[CV] m

[Parallel(n_jobs=1)]: Done  50 out of  50 | elapsed:  1.3min finished


In [33]:
gs_mnb.best_estimator_.get_params()

{'memory': None,
 'steps': [('tfidf',
   TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
                   dtype=<class 'numpy.float64'>, encoding='utf-8',
                   input='content', lowercase=True, max_df=1.0, max_features=None,
                   min_df=1, ngram_range=(1, 2), norm='l2', preprocessor=None,
                   smooth_idf=True, stop_words=None, strip_accents=None,
                   sublinear_tf=False, token_pattern='(?u)\\b\\w\\w+\\b',
                   tokenizer=None, use_idf=True, vocabulary=None)),
  ('mnb', MultinomialNB(alpha=0.1, class_prior=None, fit_prior=True))],
 'verbose': False,
 'tfidf': TfidfVectorizer(analyzer='word', binary=False, decode_error='strict',
                 dtype=<class 'numpy.float64'>, encoding='utf-8',
                 input='content', lowercase=True, max_df=1.0, max_features=None,
                 min_df=1, ngram_range=(1, 2), norm='l2', preprocessor=None,
                 smooth_idf=True, stop_words=None

In [42]:
cv_results = gs_mnb.cv_results_
results_df = pd.DataFrame({'rank': cv_results['rank_test_score'],
                           'params': cv_results['params'], 
                           'cv score (mean)': cv_results['mean_test_score'], 
                           'cv score (std)': cv_results['std_test_score']} 
              )
results_df = results_df.sort_values(by=['rank'], ascending=True)
pd.set_option('display.max_colwidth', 100)
results_df

rank                                                params  \
7     1     {'mnb__alpha': 0.1, 'tfidf__ngram_range': (1, 2)}   
8     2       {'mnb__alpha': 1, 'tfidf__ngram_range': (1, 1)}   
9     2       {'mnb__alpha': 1, 'tfidf__ngram_range': (1, 2)}   
6     4     {'mnb__alpha': 0.1, 'tfidf__ngram_range': (1, 1)}   
4     5    {'mnb__alpha': 0.01, 'tfidf__ngram_range': (1, 1)}   
0     6   {'mnb__alpha': 1e-05, 'tfidf__ngram_range': (1, 1)}   
2     6  {'mnb__alpha': 0.0001, 'tfidf__ngram_range': (1, 1)}   
5     8    {'mnb__alpha': 0.01, 'tfidf__ngram_range': (1, 2)}   
3     9  {'mnb__alpha': 0.0001, 'tfidf__ngram_range': (1, 2)}   
1    10   {'mnb__alpha': 1e-05, 'tfidf__ngram_range': (1, 2)}   

   cv score (mean)  cv score (std)  
7         0.725396        0.001170  
8         0.724830        0.000719  
9         0.724830        0.000719  
6         0.722002        0.002453  
4         0.718326        0.007242  
0         0.717760        0.007327  
2         0.717760        0.006858  
5         0.716629        0.008815  
3         0.715498        0.004385  
1         0.714932        0.004699

In [46]:

best_mnb_test_score = gs_mnb.score(test_corpus, test_label_nums)
print('Test Accuracy :', best_mnb_test_score)

Test Accuracy : 0.7246127366609294


In [48]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV

lr_pipeline = Pipeline([('tfidf', TfidfVectorizer()),
                        ('lr', LogisticRegression(penalty='l2', max_iter=100, random_state=42))
                       ])

param_grid = {'tfidf__ngram_range': [(1, 1), (1, 2)],
              'lr__C': [1, 5, 10]
}

gs_lr = GridSearchCV(lr_pipeline, param_grid, cv=5, verbose=2)
gs_lr = gs_lr.fit(train_corpus, train_label_nums)

Fitting 5 folds for each of 6 candidates, totalling 30 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] lr__C=1, tfidf__ngram_range=(1, 1) ..............................


C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


[CV] ............... lr__C=1, tfidf__ngram_range=(1, 1), total=   0.8s


...

C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


[CV] .............. lr__C=10, tfidf__ngram_range=(1, 2), total=   3.5s
[CV] lr__C=10, tfidf__ngram_range=(1, 2) .............................


C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


[CV] .............. lr__C=10, tfidf__ngram_range=(1, 2), total=   3.5s


[Parallel(n_jobs=1)]: Done  30 out of  30 | elapsed:  1.1min finished
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:469: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


In [49]:
gs_lr.best_estimator_

Pipeline(memory=None,
         steps=[('tfidf',
                 TfidfVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.float64'>,
                                 encoding='utf-8', input='content',
                                 lowercase=True, max_df=1.0, max_features=None,
                                 min_df=1, ngram_range=(1, 2), norm='l2',
                                 preprocessor=None, smooth_idf=True,
                                 stop_words=None, strip_accents=None,
                                 sublinear_tf=False,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=None, use_idf=True,
                                 vocabulary=None)),
                ('lr',
                 LogisticRegression(C=10, class_weight=None, dual=False,
                                    fit_intercept=True, intercept_scaling=1

In [50]:
predictions1 = gs_lr.predict(test_df['Clean Text'])
predictions1

array([2, 2, 2, ..., 2, 2, 2], dtype=int64)

In [51]:
sub1=pd.read_csv('sample_submission_i5xnIZD.csv')
sub1.shape

(2924, 2)

In [53]:
sub1.sentiment=predictions1

In [34]:
predictions = gs_mnb.predict(test_df['Clean Text'])
predictions

array([2, 2, 2, ..., 2, 2, 2], dtype=int64)

In [55]:
import model_evaluation_utils as meu

mnb_predictions = gs_mnb.predict(test_corpus)
unique_classes = list(set(test_label_nums))
meu.get_metrics(true_labels=test_label_nums, predicted_labels=mnb_predictions)

Accuracy: 0.7246
Precision: 0.7174
Recall: 0.7246
F1 Score: 0.6116


In [56]:
meu.display_classification_report(true_labels=test_label_nums, 
                                  predicted_labels=mnb_predictions, classes=unique_classes)

              precision    recall  f1-score   support

           0       1.00      0.01      0.01       190
           1       0.50      0.01      0.01       291
           2       0.72      1.00      0.84      1262

    accuracy                           0.72      1743
   macro avg       0.74      0.34      0.29      1743
weighted avg       0.72      0.72      0.61      1743



In [54]:
sub1.to_csv('result2.csv')

In [35]:
predictions.shape

(2924,)

In [37]:
predictions

array([2, 2, 2, ..., 2, 2, 2], dtype=int64)

In [38]:
sub=pd.read_csv('sample_submission_i5xnIZD.csv')
sub.shape

(2924, 2)

In [39]:
sub.head()

unique_hash  sentiment
0  9e9a8166b84114aca147bf409f6f956635034c08          0
1  e747e6822c867571afe7b907b51f0f2ca67b0e1a          0
2  50b6d851bcff4f35afe354937949e9948975adf7          0
3  7f82ec2176ae6ab0b5d20b5ffc767ac829f384ae          0
4  8b37d169dee5bdae27060949242fb54feb6a7f7f          0

In [40]:
sub.sentiment=predictions

In [41]:
sub.to_csv('result1.csv')

In [32]:
# # build train and test datasets
train_reviews = reviews[:3959]
train_sentiments = sentiments[:3959]
test_reviews = reviews[3959:]
test_sentiments = sentiments[3959:]

In [34]:
# test dataset
test_df= pd.read_csv('test_tOlRoBf.csv')
test_df.shape

(2924, 3)

In [35]:
test_df.head()

unique_hash  \
0  9e9a8166b84114aca147bf409f6f956635034c08   
1  e747e6822c867571afe7b907b51f0f2ca67b0e1a   
2  50b6d851bcff4f35afe354937949e9948975adf7   
3  7f82ec2176ae6ab0b5d20b5ffc767ac829f384ae   
4  8b37d169dee5bdae27060949242fb54feb6a7f7f   

                                                text        drug  
0  256 (previously stable on natalizumab), with 5...  fingolimod  
1  On fingolimod and have been since December 201...  fingolimod  
2  Apparently it's shingles! :-/ I do have a few ...      humira  
3  If the Docetaxel doing once a week x3 weeks th...    tagrisso  
4  CC, Stelara worked in a matter of days for me....     stelara

In [37]:
test_df_reviews= np.array(test_df['text'])

In [38]:
# normalize datasets
stop_words = nltk.corpus.stopwords.words('english')
stop_words.remove('no')
stop_words.remove('but')
stop_words.remove('not')

norm_train_reviews = tn.normalize_corpus(train_reviews, stopwords=stop_words)
norm_test_reviews = tn.normalize_corpus(test_reviews, stopwords=stop_words)
norm_test_df_reviews = tn.normalize_corpus(test_df_reviews, stopwords=stop_words)

In [39]:
norm_train_reviews

['autoimmune disease tend come cluster gilenya feel good not think not change anything but waste time energy take tysabri feel amazing no symptom dodgy color vision but since always not know not know last month year decade decide enjoy ride no point worry',
 'completely understand would want try but result report lecture not always stand scrutiny peer review publication much still convince hope work really aware happy risk great think important present balanced way understand not move straight first show promise animal study use drug human still lot animal datum gather human datum gather anyone tell safe effective not tell many time animal study not follow human but one major attrition point drug development unpredictability issue cladribine gilenya interaction not predict but people try doctor see pattern work go clemastine metformin exciting give say current condition personal risk tolerance make sense try definitely would not everyone',
 'interesting target sp receptor rather like f

In [40]:
norm_test_reviews

['last infusion april due another june but cancel concern start entyvio infusion add chemical body time reaction chemical already system accord information gather remicade stay system month really loss answer doctor no help thank much input rely point find guidance intelligent answer suffer crohns colitis rectal stricture dilation try humira month fail develop colon abscess occasion emergency surgery remove left side colon rectum permanent colostomy second operation remove rectal stump anus',
 'stumbler thank link yes get flu vaccine year vaccination sarahirwin not realize sinus problem side effect tysabri always sinus problem every fall get sinus infection lucky not last june also jcv positive but neurologist recommend tysabri ocrevus much activity show last two mri really hope tysabri would make feel great stop ms couple year but not think ok pml risk go make sick hard tell develop pml go make appointment neipuroligist discuss sure take month plus another couple month insurance appro

In [41]:
norm_test_df_reviews

['previously stable natalizumab switching fingolimod',
 'fingolimod since december way describe well like feel drunk but without drink',
 'apparently shingle red spot left breast appear day ago not sure connect not but show gp immediately say shingle apparently cos leave day late prescribe anything shingle gp prescribe useless amitryptiline probably not take even low dose make unbearably groggy still not entirely happy cos stomach pain bad lot bloating stuff no fever far know anyone experience shingle seem like expect week dx crohns june yay try asas azathioprine mp remicade methotrexate humira diet st surgery subtotal colectomy end ileostomy nd surgery ileorectal anastomosis stoma reverse ileum connect rectum current status chronic flare kind current med mg mp entyvio start',
 'docetaxel week x week week claim less harsh efficacy every week diagnose stage nsclc egfr also positive year tarceva month rociletinib wbr follow month tarcrva pulse carboplatin avastin alimta month tagrisso di

In [42]:
# Feature Engineering
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

# build BOW features on train reviews
cv = CountVectorizer(binary=False, min_df=0.0, max_df=1.0, ngram_range=(1,2))
cv_train_features = cv.fit_transform(norm_train_reviews)
# build TFIDF features on train reviews
tv = TfidfVectorizer(use_idf=True, min_df=0.0, max_df=1.0, ngram_range=(1,2),
                     sublinear_tf=True)
tv_train_features = tv.fit_transform(norm_train_reviews)

In [43]:
## transform test reviews into features
cv_test_features = cv.transform(norm_test_reviews)
tv_test_features = tv.transform(norm_test_reviews)

In [44]:
#transform test data reviews into features
cv_test_features_df = cv.transform(norm_test_df_reviews)
tv_test_features_df = tv.transform(norm_test_df_reviews)

In [45]:

print('BOW model:> Train features shape:', cv_train_features.shape, ' Test features shape:', cv_test_features.shape)
print('TFIDF model:> Train features shape:', tv_train_features.shape, ' Test features shape:', tv_test_features.shape)

BOW model:> Train features shape: (3959, 396525)  Test features shape: (1320, 396525)
TFIDF model:> Train features shape: (3959, 396525)  Test features shape: (1320, 396525)


In [47]:

print('BOW model: Test features shape:', cv_test_features_df.shape)
print('TFIDF model:Test features shape:', tv_test_features_df.shape)

BOW model: Test features shape: (2924, 396525)
TFIDF model:Test features shape: (2924, 396525)


In [ ]:
from sklearn.naive_bayes import MultinomialNB
mnb = MultinomialNB(alpha=1)
mnb.fit(cv_train_features, train_label_names)

In [48]:
# Model Training, Prediction and Performance Evaluatio

from sklearn.linear_model import SGDClassifier, LogisticRegression

lr = LogisticRegression(penalty='l2', max_iter=100, C=1)
svm = SGDClassifier(loss='hinge', max_iter=100)

In [49]:
# Logistic Regression model on BOW features
lr_bow_predictions = meu.train_predict_model(classifier=lr, 
                                             train_features=cv_train_features, train_labels=train_sentiments,
                                             test_features=cv_test_features, test_labels=test_sentiments)
meu.display_model_performance_metrics(true_labels=test_sentiments, predicted_labels=lr_bow_predictions,
                                      classes=['positive', 'negative','neutral'])

C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:460: FutureWarning: Default multi_class will be changed to 'auto' in 0.22. Specify the multi_class option to silence this warning.
  "this warning.", FutureWarning)


Model Performance metrics:
------------------------------
Accuracy: 0.7159
Precision: 0.666
Recall: 0.7159
F1 Score: 0.6732

Model Classification report:
------------------------------


C:\Users\Rohit Gupta\Anaconda3\lib\site-packages\numpy\lib\arraysetops.py:565: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask &= (ar1 != a)


ValueError: y contains previously unseen labels: [0, 1, 2]